In [1]:
from datasets import load_dataset
from models.unigram_trainer import UnigramTrainer
from transformers import PreTrainedTokenizerFast
from phonemizer import phonemize
from phonemizer.separator import Separator

### Loading the training dataset

- `combined_hibn_corpus`: Bilingual (hi + bn) Corpus
- `combined_hibn_phonemized_corpus`: Bilingual (hi + bn) Phonemized Corpus

Both the corpus have word-to-word correspondences between the native and phonemized text. One thing to note is that phonemized version doesn't have any punctuation (TODO: Resolve later).

This notebook has sample usage for combined corpus. 

To separate the corpus into individual languages into different folders (required in case of training a monolingual tokenizer), use the following -
- `combined_hibn_corpus` has both Hindi and Bengali text files in the form `sample_XXX.txt` and `bn_sample_XXX.txt` respectively.
- `combined_hibn_phonemized_corpus` has both Hindi and Bengali text files in the form `phn_sample_XXX.txt` and `bn_phn_sample_XXX.txt` respectively.

In [2]:
%%time
# Native language corpus

ds = load_dataset("parquet", data_files={'train': 'data/combined_hibn_corpus.parquet'})
ds = ds['train'] # Select the train split (All data in the directory is loaded as train split if not otherwise specified)

CPU times: user 152 ms, sys: 242 ms, total: 394 ms
Wall time: 3.43 s


In [3]:
%%time
# Phonemized language corpus

phon_ds = load_dataset("parquet", data_files={'train': 'data/combined_hibn_phonemized_corpus.parquet'})
phon_ds = phon_ds['train']

CPU times: user 66.4 ms, sys: 81.8 ms, total: 148 ms
Wall time: 2.21 s


### Trainer

In [4]:
%%time
# Train a native lang tokenizer, change dataset = ds and save it to an output directory
UnigramTrainer(dataset=ds, vocab_size=8000, batch_size=10000, output_dir="hibn_unigramtokenizer_8k")



CPU times: user 1h 16min 23s, sys: 3min 36s, total: 1h 20min
Wall time: 6min 14s


In [5]:
%%time
# Train a phonemized lang tokenizer, change dataset = phon_ds
UnigramTrainer(dataset=phon_ds, vocab_size=8000, batch_size=10000, output_dir="hibn_phn_unigramtokenizer_8k")



CPU times: user 40min 2s, sys: 39.5 s, total: 40min 41s
Wall time: 3min 1s


### Load the trained tokenizers

In [6]:
baseline_tokenizer = PreTrainedTokenizerFast.from_pretrained("hibn_unigramtokenizer_8k") # input directory for the saved tokenizer
phoneme_tokenizer = PreTrainedTokenizerFast.from_pretrained("hibn_phn_unigramtokenizer_8k")

### Testing the tokenizers

In [7]:
test_string_hi = 'बहुत ही पुरानी बात है,ये कहानी है सुन्दर फूलों की दुनिया की है जहा बहुत से सुन्दर सुन्दर  फूल है जो आपस में बाते करते है खेलते है और बहुत खुश रहते है  एक सुंदर जगह जहां हर किसी फूल का दिल खुश था। जो एक अनोखी दुनिया है जो फूलों से महकती है। उसी सुन्दर जगह में बहुत सुन्दर गुलाब नाम का फूल रहता था। गुलाब, जैसा कि उसका नाम है, फूलों के के बीच रहने रहने वाला बहुत प्यार फूल था। उसका सपना था कि वह सभी फूलों की दुनिया में घूमे और और उन्हें देखे वे कितने सुन्दर है जो उसके ही जैसे है वह उनसे बातें करे।'
test_string_bn = 'এখনই তো খাবার বয়স, অথচ পকেটমানি জোটে না। ওদিকে হিরুদা আর ধীরুদার গলায় গলায় বন্ধুত্ব। কেন ওদের জুটি অটুট তাও জানে বিল্টু-মিল্টু। ওরা ভোজনা বাড়িতে বিনা নিমন্ত্রণে, বিনামূল্যে গান্ডে পিন্ডে গিলে আসে। অনুষ্ঠানের হলের আশেপাশে ঘাপটি মেরে অপেক্ষা করে, যেই কনেযাত্রী বা বরযাত্রীর দল ঢোকে, ওদের সঙ্গে মিশে যায়। কোন তরফের অতিথি কেউ বুঝতে পারেনা।ভোলাদার চায়ের দোকানের ঠেকে ব্যঙ্গ করে হীরুদা বলে, মজার খবর বোম্বাইের এক রেস্টুরেন্টে খাবারের বিল না মেটানোর জন্য কাপ-ডিশ ধুইয়ে ছেড়ে দিয়েছে। বিল্টু, মিল্টুকে বলে এইরকম একটা রেস্টুরেন্ট যদি এখানে থাকত বেশি বেশি করে ডিশ ধুয়ে দিতাম। হিরুদা খবর পরিবেশন করল, অনাবাসী কয়েকজন ভারতীয় ম্যাগনাম রেস্টুরেন্ট খুলেছে। সেখানে নাকি বিল মেটাতে পারেনি বলে, জামা খুলে জমা রেখেছে। বিল মিটিয়ে জামা ফেরত নিতে হবে।ওরা রেস্টুরেন্টটা খুঁজে পেল। দেখতে পেল একধারে পুরনো জামা কাপড় সুন্দর করে ঝোলানো আছে। তাহলে খবরটি মিথ্যে নয়। বেশি খাবারের অর্ডার দিল না প্রথম দিন রয়ে সয়ে খাওয়া ভাল। ম্যাগনাম আমাদের মাগনায় দেবে। কাউন্টারে দাম দেওয়ার সময় বলল, “আমাদের মানিব্যাগটা মনে হয় কোথাও পড়ে গেছে। দাম দিতে পারছি না, পরে দিয়ে যাব।” ম্যানেজার বলল, “ঠিক আছে ভাই তোমাদের জামাটা খুলে রেখে যাও পয়সা দিয়ে নিয়ে যেও।” বাইরে এসে বিল্টু বলে, “কেন তোকে বলেছিলাম রঙিন গেঞ্জি পড়ে আসতে এখন বুঝলি?” মিল্টু বলে, “রাস্তার লোকরা জানতে পারবেনা আমরা জামা রেস্টুরেন্টে বন্ধক রেখেছি।” খুব খুশি। এত দিনে মনের মতো একটা রেস্টুরেন্ট হয়েছে। যুগ যুগ জিও। কিছুদিনের মধ্যেই ওরা আবার হাজির। দেখলো ওদের জামাগুলো টাঙানো আছে। ভারিক্কি গলায় ভাল ভাল খাবারের অর্ডার দিল। বেয়ারা একগ্লাস শরবত ধরিয়ে দিয়ে বলে, “ম্যনেজার সাহেব বলেছেন খাবার তৈরি করতে একটু সময় লাগবে। আপনারা ততক্ষণ বিনি পয়সার শরবত খান।”শরবত অর্ধেক শেষ হয়েছে। পেট মোচড় দিয়ে উঠল। আর থাকতে পারছে না দুজনেই ছুটল বাথরুমে। ম্যনেজার বাথরুমে তালা লাগিয়ে বলে, “আমাদের ফটো আইডেন্টি মেশিনে ধরা পড়েছে, বিল মেটাওনি। পুলিশে খবর দেওয়া হয়েছে। ওরাই ব্যবস্থা নেবে।'

In [8]:
# phonemize both the test strings
# phonemize func takes input as a list of strings instead of a single string, input is [test_string_hi]
# The output is also a list, to access the phonemized string, use phonemized_hi[0]

phonemized_hi = phonemize(
            [test_string_hi],
            language = 'hi',
            backend = 'espeak',
            separator = Separator(phone = None, word = ' ', syllable = None),
            strip = True,
            language_switch='remove-flags',
            preserve_punctuation = True,
            njobs = 1
        )

phonemized_bn = phonemize(
            [test_string_bn],
            language = 'bn',
            backend = 'espeak',
            separator = Separator(phone = None, word = ' ', syllable = None),
            strip = True,
            language_switch='remove-flags',
            preserve_punctuation = True,
            njobs = 1
        )

In [9]:
# Hindi test

hi_words = test_string_hi.split()
hi_phn_words = phonemized_hi[0].split()
print("Number of Hindi words:",len(hi_words))
print("Number of phonemized Hindi words:",len(hi_phn_words))

# Bengali test

bn_words = test_string_bn.split()
bn_phn_words = phonemized_bn[0].split()
print("Number of Bengali words:",len(bn_words))
print("Number of phonemized Bengali words:",len(bn_phn_words))

Number of Hindi words: 111
Number of phonemized Hindi words: 111
Number of Bengali words: 290
Number of phonemized Bengali words: 292


#### Test on Hindi

In [10]:
print("Number of baseline tokens:",len(baseline_tokenizer.encode(test_string_hi)))
print(baseline_tokenizer.tokenize(test_string_hi))
print("Number of phoneme tokens:",len(phoneme_tokenizer.encode(phonemized_hi[0])))
print(phoneme_tokenizer.tokenize(phonemized_hi[0]))

Number of baseline tokens: 143
['▁बहुत', '▁ही', '▁पुरानी', '▁बात', '▁है,', 'ये', '▁कहानी', '▁है', '▁सु', 'न्द', 'र', '▁फूल', 'ों', '▁की', '▁दुनिया', '▁की', '▁है', '▁ज', 'हा', '▁बहुत', '▁से', '▁सु', 'न्द', 'र', '▁सु', 'न्द', 'र', '▁फूल', '▁है', '▁जो', '▁आप', 'स', '▁में', '▁बात', 'े', '▁करते', '▁है', '▁खेल', 'ते', '▁है', '▁और', '▁बहुत', '▁खुश', '▁रहते', '▁है', '▁एक', '▁सुंदर', '▁जगह', '▁जहां', '▁हर', '▁किसी', '▁फूल', '▁का', '▁दिल', '▁खुश', '▁था।', '▁जो', '▁एक', '▁अन', 'ो', 'ख', 'ी', '▁दुनिया', '▁है', '▁जो', '▁फूल', 'ों', '▁से', '▁मह', 'क', 'ती', '▁है।', '▁उसी', '▁सु', 'न्द', 'र', '▁जगह', '▁में', '▁बहुत', '▁सु', 'न्द', 'र', '▁गुलाब', '▁नाम', '▁का', '▁फूल', '▁रहता', '▁था।', '▁गुलाब', ',', '▁जैसा', '▁कि', '▁उसका', '▁नाम', '▁है,', '▁फूल', 'ों', '▁के', '▁के', '▁बीच', '▁रहने', '▁रहने', '▁वाला', '▁बहुत', '▁प्यार', '▁फूल', '▁था।', '▁उसका', '▁सपना', '▁था', '▁कि', '▁वह', '▁सभी', '▁फूल', 'ों', '▁की', '▁दुनिया', '▁में', '▁घूम', 'े', '▁और', '▁और', '▁उन्हें', '▁देख', 'े', '▁वे', '▁कितने', '▁सु', 'न्द'

#### Test on Bengali

In [11]:
print("Number of baseline tokens:",len(baseline_tokenizer.encode(test_string_bn)))
print(baseline_tokenizer.tokenize(test_string_bn))
print("Number of phoneme tokens:",len(phoneme_tokenizer.encode(phonemized_bn[0])))
print(phoneme_tokenizer.tokenize(phonemized_bn[0]))

Number of baseline tokens: 631
['▁এখন', 'ই', '▁তো', '▁খাবার', '▁বয়স', ',', '▁অথচ', '▁প', 'কে', 'ট', 'মান', 'ি', '▁জো', 'টে', '▁না।', '▁ও', 'দিকে', '▁হি', 'রু', 'দা', '▁আর', '▁ধ', 'ী', 'রু', 'দার', '▁গ', 'লায়', '▁গ', 'লায়', '▁বন্ধু', 'ত্ব', '।', '▁কেন', '▁ও', 'দের', '▁জু', 'টি', '▁অ', 'টু', 'ট', '▁তা', 'ও', '▁জা', 'নে', '▁বি', 'ল্ট', 'ু', '-', 'মি', 'ল্ট', 'ু', '।', '▁ও', 'রা', '▁', 'ভো', 'জ', 'না', '▁বাড়িতে', '▁বি', 'না', '▁নি', 'ম', 'ন্ত্র', 'ণ', 'ে', ',', '▁বিনামূল্যে', '▁গা', 'ন্ড', 'ে', '▁পি', 'ন্ড', 'ে', '▁', 'গি', 'লে', '▁আসে', '।', '▁অনুষ্ঠানে', 'র', '▁হলে', 'র', '▁আ', 'শে', 'পা', 'শে', '▁ঘ', 'া', 'প', 'টি', '▁মে', 'রে', '▁অপেক্ষা', '▁করে', ',', '▁যে', 'ই', '▁কন', 'ে', 'যা', 'ত্রী', '▁বা', '▁বর', 'যা', 'ত্রী', 'র', '▁দল', '▁ঢে', 'া', 'কে', ',', '▁ও', 'দের', '▁সঙ্গে', '▁মি', 'শে', '▁যায়।', '▁কোন', '▁তর', 'ফ', 'ের', '▁অতিথি', '▁কেউ', '▁বুঝতে', '▁পারেন', 'া।', 'ভো', 'লা', 'দার', '▁চায়', 'ের', '▁দোকান', 'ের', '▁', 'ঠ', 'ে', 'কে', '▁', 'ব্য', 'ঙ্গ', '▁করে', '▁হ', 'ী', 'রু